### LLAMA

In [ ]:

!pip install transformers accelerate sentencepiece datasets openai fuzzywuzzy


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 19.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 117.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 91.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 60.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
from tqdm import tqdm
from itertools import islice

start_index = 0
end_index = 500

train_subset = list(islice(train_dataset, 500))
test_subset = list(islice(test_dataset, 500, 1000))


### Few shot

### Zero Shot

In [ ]:
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from fuzzywuzzy import fuzz
import re

SIMILARITY_THRESHOLD = 0.8
FUZZY_MATCH_THRESHOLD = 80
start_index = 0
end_index = 500
output_file_path = "zero_shot_acronym_expansion_results_gpt3-5.txt"

from itertools import islice
test_subset = list(islice(test_dataset, 500, 1000))

from openai import OpenAI


client = OpenAI(api_key="OPENAI_API_KEY")


embedding_model = SentenceTransformer('all-MiniLM-L6-v2')

def build_prompt(context, acronym, entities, abstract_id="N/A"):
    return (
        f"You are a biomedical language model. Given the following clinical text snippet, "
        f"identify the most likely expansion of the acronym.\n\n"
        f"Text snippet:\n{context}\n\n"
        f"Your task is to expand the acronym '{acronym}' based on this context.\n"
        f"Answer only in the format: {acronym}, Full Form\n\n"
        f"Answer:"
    )

def preprocess_expansion(expansion):
    return re.sub(r'[^a-zA-Z0-9]', '', expansion).lower()

def is_semantic_match(predicted_expansion, labels, threshold=SIMILARITY_THRESHOLD):
    if not predicted_expansion or not labels:
        return False, 0.0
    try:
        pred_processed = preprocess_expansion(predicted_expansion)
        pred_emb = embedding_model.encode([pred_processed])[0]
        label_processed = [preprocess_expansion(label) for label in labels]
        label_embs = embedding_model.encode(label_processed)
        similarities = cosine_similarity([pred_emb], label_embs)[0]
        best_sim = max(similarities)

        fuzzy_matches = [fuzz.ratio(pred_processed, label) for label in label_processed]
        best_fuzzy = max(fuzzy_matches)

        match = best_sim >= threshold or best_fuzzy >= FUZZY_MATCH_THRESHOLD
        return match, best_sim
    except Exception as e:
        print(f"Embedding error: {e}")
        return False, 0.0

correct = 0
total = 0
output_lines = []

for i in tqdm(range(start_index, end_index), desc="Running Zero-Shot Inference"):
    if i >= len(test_subset):
        break

    test_sample = test_subset[i]
    if not test_sample:
        print(f"⚠️ Skipping empty entry at index {i}")
        continue

    test_context = test_sample['text']
    test_label = test_sample['label']
    test_location = test_sample['location']
    test_entities = test_sample.get('entities', [])
    test_abstract_id = test_sample.get('abstract_id', f"Test-{i}")
    test_acronym = test_context.split(' ')[test_location[0]]

    # Build final test prompt (zero-shot)
    test_prompt = build_prompt(test_context, test_acronym, test_entities)
    full_prompt = test_prompt

    print(full_prompt)



    response = client.chat.completions.create(
        model="gpt-3.5-turbo",
        messages=[{"role": "user", "content": full_prompt}],
        temperature=0.2,
        max_tokens=20
    )

    output = response.choices[0].message.content.strip()

    try:
        predicted_acronym, predicted_expansion = [part.strip() for part in output.split(',', 1)]
    except ValueError:
        predicted_acronym, predicted_expansion = "", ""

    label_list = test_label if isinstance(test_label, list) else [test_label]
    acronym_match = predicted_acronym.lower() == test_acronym.lower()
    semantic_match, similarity = is_semantic_match(predicted_expansion, label_list)
    match_status = '✔️' if acronym_match and semantic_match else '❌'

    print("=" * 80)
    print(f"Index                 : {i}")
    print(f"Acronym               : {test_acronym}")
    print(f"Predicted             : {predicted_acronym} → {predicted_expansion}")
    print(f"Actual (Ground Truth) : {test_acronym} → {label_list}")
    print(f"📏 Cosine Similarity   : {similarity:.3f}")
    print(f"🎯 Match               : {match_status}")
    print("=" * 80)

    output_lines.append(
        f"Index                 : {i}\n"
        f"Acronym               : {test_acronym}\n"
        f"Predicted             : {predicted_acronym} → {predicted_expansion}\n"
        f"Actual (Ground Truth) : {test_acronym} → {label_list}\n"
        f"📏 Cosine Similarity   : {similarity:.3f}\n"
        f"🎯 Match               : {match_status}\n"
        + "=" * 80 + "\n"
    )

    if acronym_match and semantic_match:
        correct += 1
    total += 1

    # break

accuracy = correct / total if total > 0 else 0
summary_line = f"\n✅ Final Semantic Similarity Accuracy (threshold={SIMILARITY_THRESHOLD}): {accuracy:.2%}\n"
print(summary_line)

with open(output_file_path, 'w', encoding='utf-8') as f:
    f.writelines(output_lines)
    f.write(summary_line)

print(f"📁 Results saved to: {output_file_path}")


Running Zero-Shot Inference:   0%|          | 0/500 [00:00<?, ?it/s]

You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
we evaluated the effects of FF cysteinerich FM or iu of vitamin e for d before slaughter on the rates of death and emergency slaughter due to AIP aip in commercial feedlots blood and lung tissue were collected at slaughter from animals clinically diagnosed with aip asymptomatic penmates and heifers receiving either FM or VE the left lung was subsampled for histologic examination blood and lung tissue were analyzed for thiol adducts of methyleneindolenine me and reduced glutathione supplementation with FM or vitamin e had no effect on the rates of death and emergency slaughter attributable to aip and did not influence the C2 of me or reduced glutathione in blood or lung tissue although supplementation with greater amounts of feather meal or vitamin e may have been necessary to significantly affect factors related to feedlot aip increased suppl

Running Zero-Shot Inference:   0%|          | 1/500 [00:00<03:11,  2.61it/s]

Index                 : 0
Acronym               : FM
Predicted             : FM → Feather Meal
Actual (Ground Truth) : FM → ['feather meal']
📏 Cosine Similarity   : 1.000
🎯 Match               : ✔️
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
the ARV nonstructural protein sigma ns has previously been shown to bind singlestranded ss rna in vitro in a sequenceindependent manner the results of the present study further reveal that sigma ns binds polya polyu and ssdna but not polyc polyg or duplex nucleic acids suggesting that sigma ns has some nucleotidesequence specificity for ssrna binding the current findings also show that sigma ns is present in C1 ribonucleoprotein complexes in the cytoplasm of avian reovirusinfected cells indicating that it exists in intimate association with ssrnas in vivo removal of rna from the complexes generates a sigma ns protein form that sediments between and

Running Zero-Shot Inference:   0%|          | 2/500 [00:00<04:11,  1.98it/s]

...

Index                 : 497
Acronym               : UCVA
Predicted             : UCVA → Uncorrected Visual Acuity
Actual (Ground Truth) : UCVA → ['uncorrected']
📏 Cosine Similarity   : 0.471
🎯 Match               : ❌
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
two physically and genetically distinct forms of RPI have been identified in escherichia coli k the constitutive ribosephosphate isomerase a has a km for ribose phosphate mm six times greater than that of the inducible RPI b mm treatment of the enzymes with mm IAA resulted in loss of activity for RPI b whereas ribosephosphate isomerase a was unaffected various cellular metabolites were tested and found to be without significant effect on either enzyme the two enzymes could be separated by filtration on sephadex g superfine and their apparent molecular weights were for RPI a and for ribosephosphate isomerase b under certain condit

Running Zero-Shot Inference: 100%|█████████▉| 499/500 [04:35<00:00,  1.12it/s]

Index                 : 498
Acronym               : RPI
Predicted             : RPI → Ribosephosphate Isomerase
Actual (Ground Truth) : RPI → ['ribosephosphate isomerase']
📏 Cosine Similarity   : 1.000
🎯 Match               : ✔️
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
induction of cellular detoxification enzymes can increase detoxification of carcinogens and reduce carcinogeninduced mutagenesis and tumorigenesis to determine if the dietary anticarcinogen ellagic acid induced enzymes which detoxify xenobiotics and carcinogens we examined the effect of EA on the expression of the phase ii detoxification enzyme nadphquinone reductase qr qr is induced by xenobiotics and antioxidants interacting with the xenobiotic responsive and antioxidant HRE of the regulatory region of the qr gene EA is structurally related to the antioxidants which induce qr and we proposed that EA would induce qr 

Running Zero-Shot Inference: 100%|██████████| 500/500 [04:36<00:00,  1.81it/s]

Index                 : 499
Acronym               : ARE
Predicted             : ARE → Antioxidant Response Element
Actual (Ground Truth) : ARE → ['antioxidant responsive element']
📏 Cosine Similarity   : 0.881
🎯 Match               : ✔️

✅ Final Semantic Similarity Accuracy (threshold=0.8): 74.00%

📁 Results saved to: zero_shot_acronym_expansion_results_gpt3-5.txt


### Zero-shot GPT-4

In [ ]:
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from fuzzywuzzy import fuzz
import re

# --- Config ---
SIMILARITY_THRESHOLD = 0.8
FUZZY_MATCH_THRESHOLD = 80
start_index = 0
end_index = 500
output_file_path = "zero_shot_acronym_expansion_results_gpt4.txt"

# --- Dataset setup ---
from itertools import islice
test_subset = list(islice(test_dataset, 500, 1000))

# --- OpenAI client (assumed already authenticated) ---
from openai import OpenAI

client = OpenAI(api_key="OPENAI_API_KEY")


embedding_model = SentenceTransformer('all-MiniLM-L6-v2')

def build_prompt(context, acronym, entities, abstract_id="N/A"):
    return (
        f"You are a biomedical language model. Given the following clinical text snippet, "
        f"identify the most likely expansion of the acronym.\n\n"
        f"Text snippet:\n{context}\n\n"
        f"Your task is to expand the acronym '{acronym}' based on this context.\n"
        f"Answer only in the format: {acronym}, Full Form\n\n"
        f"Answer:"
    )

# --- Helper functions ---
def preprocess_expansion(expansion):
    return re.sub(r'[^a-zA-Z0-9]', '', expansion).lower()

def is_semantic_match(predicted_expansion, labels, threshold=SIMILARITY_THRESHOLD):
    if not predicted_expansion or not labels:
        return False, 0.0
    try:
        pred_processed = preprocess_expansion(predicted_expansion)
        pred_emb = embedding_model.encode([pred_processed])[0]
        label_processed = [preprocess_expansion(label) for label in labels]
        label_embs = embedding_model.encode(label_processed)
        similarities = cosine_similarity([pred_emb], label_embs)[0]
        best_sim = max(similarities)

        fuzzy_matches = [fuzz.ratio(pred_processed, label) for label in label_processed]
        best_fuzzy = max(fuzzy_matches)

        match = best_sim >= threshold or best_fuzzy >= FUZZY_MATCH_THRESHOLD
        return match, best_sim
    except Exception as e:
        print(f"Embedding error: {e}")
        return False, 0.0

correct = 0
total = 0
output_lines = []

for i in tqdm(range(start_index, end_index), desc="Running Zero-Shot Inference"):
    if i >= len(test_subset):
        break

    test_sample = test_subset[i]
    if not test_sample:
        print(f"⚠️ Skipping empty entry at index {i}")
        continue

    test_context = test_sample['text']
    test_label = test_sample['label']
    test_location = test_sample['location']
    test_entities = test_sample.get('entities', [])
    test_abstract_id = test_sample.get('abstract_id', f"Test-{i}")
    test_acronym = test_context.split(' ')[test_location[0]]

    test_prompt = build_prompt(test_context, test_acronym, test_entities)
    full_prompt = test_prompt

    print(full_prompt)



    response = client.chat.completions.create(
        model="gpt-4",
        messages=[{"role": "user", "content": full_prompt}],
        temperature=0.2,
        max_tokens=20
    )

    output = response.choices[0].message.content.strip()

    try:
        predicted_acronym, predicted_expansion = [part.strip() for part in output.split(',', 1)]
    except ValueError:
        predicted_acronym, predicted_expansion = "", ""

    label_list = test_label if isinstance(test_label, list) else [test_label]
    acronym_match = predicted_acronym.lower() == test_acronym.lower()
    semantic_match, similarity = is_semantic_match(predicted_expansion, label_list)
    match_status = '✔️' if acronym_match and semantic_match else '❌'

    print("=" * 80)
    print(f"Index                 : {i}")
    print(f"Acronym               : {test_acronym}")
    print(f"Predicted             : {predicted_acronym} → {predicted_expansion}")
    print(f"Actual (Ground Truth) : {test_acronym} → {label_list}")
    print(f"📏 Cosine Similarity   : {similarity:.3f}")
    print(f"🎯 Match               : {match_status}")
    print("=" * 80)

    output_lines.append(
        f"Index                 : {i}\n"
        f"Acronym               : {test_acronym}\n"
        f"Predicted             : {predicted_acronym} → {predicted_expansion}\n"
        f"Actual (Ground Truth) : {test_acronym} → {label_list}\n"
        f"📏 Cosine Similarity   : {similarity:.3f}\n"
        f"🎯 Match               : {match_status}\n"
        + "=" * 80 + "\n"
    )

    if acronym_match and semantic_match:
        correct += 1
    total += 1

    # break

accuracy = correct / total if total > 0 else 0
summary_line = f"\n✅ Final Semantic Similarity Accuracy (threshold={SIMILARITY_THRESHOLD}): {accuracy:.2%}\n"
print(summary_line)

with open(output_file_path, 'w', encoding='utf-8') as f:
    f.writelines(output_lines)
    f.write(summary_line)

print(f"📁 Results saved to: {output_file_path}")


Running Zero-Shot Inference:   0%|          | 0/500 [00:00<?, ?it/s]

You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
we evaluated the effects of FF cysteinerich FM or iu of vitamin e for d before slaughter on the rates of death and emergency slaughter due to AIP aip in commercial feedlots blood and lung tissue were collected at slaughter from animals clinically diagnosed with aip asymptomatic penmates and heifers receiving either FM or VE the left lung was subsampled for histologic examination blood and lung tissue were analyzed for thiol adducts of methyleneindolenine me and reduced glutathione supplementation with FM or vitamin e had no effect on the rates of death and emergency slaughter attributable to aip and did not influence the C2 of me or reduced glutathione in blood or lung tissue although supplementation with greater amounts of feather meal or vitamin e may have been necessary to significantly affect factors related to feedlot aip increased suppl

Running Zero-Shot Inference:   0%|          | 1/500 [00:00<06:10,  1.35it/s]

Index                 : 0
Acronym               : FM
Predicted             : FM → Feather Meal
Actual (Ground Truth) : FM → ['feather meal']
📏 Cosine Similarity   : 1.000
🎯 Match               : ✔️
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
the ARV nonstructural protein sigma ns has previously been shown to bind singlestranded ss rna in vitro in a sequenceindependent manner the results of the present study further reveal that sigma ns binds polya polyu and ssdna but not polyc polyg or duplex nucleic acids suggesting that sigma ns has some nucleotidesequence specificity for ssrna binding the current findings also show that sigma ns is present in C1 ribonucleoprotein complexes in the cytoplasm of avian reovirusinfected cells indicating that it exists in intimate association with ssrnas in vivo removal of rna from the complexes generates a sigma ns protein form that sediments between and

Running Zero-Shot Inference:   0%|          | 2/500 [00:01<07:38,  1.09it/s]

...

Index                 : 497
Acronym               : UCVA
Predicted             : UCVA → Uncorrected Visual Acuity
Actual (Ground Truth) : UCVA → ['uncorrected']
📏 Cosine Similarity   : 0.471
🎯 Match               : ❌
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
two physically and genetically distinct forms of RPI have been identified in escherichia coli k the constitutive ribosephosphate isomerase a has a km for ribose phosphate mm six times greater than that of the inducible RPI b mm treatment of the enzymes with mm IAA resulted in loss of activity for RPI b whereas ribosephosphate isomerase a was unaffected various cellular metabolites were tested and found to be without significant effect on either enzyme the two enzymes could be separated by filtration on sephadex g superfine and their apparent molecular weights were for RPI a and for ribosephosphate isomerase b under certain condit

Running Zero-Shot Inference: 100%|█████████▉| 499/500 [13:37<00:01,  1.69s/it]

Index                 : 498
Acronym               : RPI
Predicted             : RPI → Ribosephosphate Isomerase
Actual (Ground Truth) : RPI → ['ribosephosphate isomerase']
📏 Cosine Similarity   : 1.000
🎯 Match               : ✔️
You are a biomedical language model. Given the following clinical text snippet, identify the most likely expansion of the acronym.

Text snippet:
induction of cellular detoxification enzymes can increase detoxification of carcinogens and reduce carcinogeninduced mutagenesis and tumorigenesis to determine if the dietary anticarcinogen ellagic acid induced enzymes which detoxify xenobiotics and carcinogens we examined the effect of EA on the expression of the phase ii detoxification enzyme nadphquinone reductase qr qr is induced by xenobiotics and antioxidants interacting with the xenobiotic responsive and antioxidant HRE of the regulatory region of the qr gene EA is structurally related to the antioxidants which induce qr and we proposed that EA would induce qr 

Running Zero-Shot Inference: 100%|██████████| 500/500 [13:39<00:00,  1.64s/it]

Index                 : 499
Acronym               : ARE
Predicted             : ARE → Antioxidant Response Element
Actual (Ground Truth) : ARE → ['antioxidant responsive element']
📏 Cosine Similarity   : 0.881
🎯 Match               : ✔️

✅ Final Semantic Similarity Accuracy (threshold=0.8): 76.20%

📁 Results saved to: zero_shot_acronym_expansion_results_gpt4.txt


In [ ]:
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from fuzzywuzzy import fuzz
import re
import torch
from transformers import BioGptTokenizer, BioGptForCausalLM

SIMILARITY_THRESHOLD = 0.8
FUZZY_MATCH_THRESHOLD = 80
FEW_SHOT_EXAMPLES = 3
start_index = 0
end_index = 500
output_file_path = "few_shot_acronym_expansion_results_biogpt.txt"
device = "cuda" if torch.cuda.is_available() else "cpu"

from itertools import islice
train_subset = list(islice(train_dataset, 500))
test_subset = list(islice(test_dataset, 500, 1000))

# --- BioGPT model ---
tokenizer = BioGptTokenizer.from_pretrained("microsoft/biogpt")
model = BioGptForCausalLM.from_pretrained("microsoft/biogpt").to(device)
model.eval()

embedding_model = SentenceTransformer('all-MiniLM-L6-v2')

# --- Prompt builder (UNCHANGED) ---
def build_prompt(context, acronym, entities, abstract_id="N/A"):
    return (
        f"You are a clinical language model helping with abbreviation disambiguation in biomedical texts.\n"
        f"Text snippet (with acronym): {context}\n"
        f"Your task is to expand the acronym '{acronym}' based on the above biomedical context.\n"
        f"Answer only with the acronym and its full form, separated by a comma.\n"
        f"Format: {acronym}, Full Form\n"
        f"Answer:"
    )

# --- Helper functions ---
def preprocess_expansion(expansion):
    return re.sub(r'[^a-zA-Z0-9]', '', expansion).lower()

def is_semantic_match(predicted_expansion, labels, threshold=SIMILARITY_THRESHOLD):
    if not predicted_expansion or not labels:
        return False, 0.0
    try:
        pred_processed = preprocess_expansion(predicted_expansion)
        pred_emb = embedding_model.encode([pred_processed])[0]
        label_processed = [preprocess_expansion(label) for label in labels]
        label_embs = embedding_model.encode(label_processed)
        similarities = cosine_similarity([pred_emb], label_embs)[0]
        best_sim = max(similarities)

        fuzzy_matches = [fuzz.ratio(pred_processed, label) for label in label_processed]
        best_fuzzy = max(fuzzy_matches)

        match = best_sim >= threshold or best_fuzzy >= FUZZY_MATCH_THRESHOLD
        return match, best_sim
    except Exception as e:
        print(f"Embedding error: {e}")
        return False, 0.0

# --- Evaluation loop ---
correct = 0
total = 0
output_lines = []

for i in tqdm(range(start_index, end_index), desc="Running Few-Shot Inference with BioGPT"):
    if i >= len(test_subset):
        break

    test_sample = test_subset[i]
    if not test_sample:
        print(f"⚠️ Skipping empty entry at index {i}")
        continue

    test_context = test_sample['text']
    test_label = test_sample['label']
    test_location = test_sample['location']
    test_entities = test_sample.get('entities', [])
    test_acronym = test_context.split(' ')[test_location[0]]

    # Build few-shot prompt examples
    few_shot_prompt = ""
    for j in range(FEW_SHOT_EXAMPLES):
        if j >= len(train_subset):
            break
        fs_sample = train_subset[j]
        if not fs_sample:
            continue
        fs_context = fs_sample['text']
        fs_label = fs_sample['label'][0] if isinstance(fs_sample['label'], list) else fs_sample['label']
        fs_location = fs_sample['location']
        fs_entities = fs_sample.get('entities', [])
        fs_acronym = fs_context.split(' ')[fs_location[0]]
        fs_prompt = build_prompt(fs_context, fs_acronym, fs_entities)
        few_shot_prompt += f"{fs_prompt} {fs_acronym}, {fs_label}\n\n"

    # Build final test prompt
    test_prompt = build_prompt(test_context, test_acronym, test_entities)
    full_prompt = few_shot_prompt + test_prompt

    print(full_prompt)




    # Call BioGPT
    inputs = tokenizer(full_prompt, return_tensors="pt").to(device)

    if inputs['input_ids'].shape[1] > 1024:
      print(f"⚠️ Skipping index {i} due to input length ({inputs['input_ids'].shape[1]} tokens)")
      continue

    outputs = model.generate(**inputs, max_new_tokens=30, do_sample=True)
    output_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

    result_line = output_text.split("Answer:")[-1].strip()
    try:
        predicted_acronym, predicted_expansion = [part.strip() for part in result_line.split(",", 1)]
    except ValueError:
        predicted_acronym, predicted_expansion = "", ""

    label_list = test_label if isinstance(test_label, list) else [test_label]
    acronym_match = predicted_acronym.lower() == test_acronym.lower()
    semantic_match, similarity = is_semantic_match(predicted_expansion, label_list)
    match_status = '✔️' if acronym_match and semantic_match else '❌'

    print("=" * 80)
    print(f"Index                 : {i}")
    print(f"Acronym               : {test_acronym}")
    print(f"Predicted             : {predicted_acronym} → {predicted_expansion}")
    print(f"Actual (Ground Truth) : {test_acronym} → {label_list}")
    print(f"📏 Cosine Similarity   : {similarity:.3f}")
    print(f"🎯 Match               : {match_status}")
    print("=" * 80)

    output_lines.append(
        f"Index                 : {i}\n"
        f"Acronym               : {test_acronym}\n"
        f"Predicted             : {predicted_acronym} → {predicted_expansion}\n"
        f"Actual (Ground Truth) : {test_acronym} → {label_list}\n"
        f"📏 Cosine Similarity   : {similarity:.3f}\n"
        f"🎯 Match               : {match_status}\n"
        + "=" * 80 + "\n"
    )

    if acronym_match and semantic_match:
        correct += 1
    total += 1

# --- Final Accuracy ---
accuracy = correct / total if total > 0 else 0
summary_line = f"\n✅ Final Semantic Similarity Accuracy (threshold={SIMILARITY_THRESHOLD}): {accuracy:.2%}\n"
print(summary_line)

with open(output_file_path, 'w', encoding='utf-8') as f:
    f.writelines(output_lines)
    f.write(summary_line)

print(f"📁 Results saved to: {output_file_path}")


Running Few-Shot Inference with BioGPT:   1%|          | 5/500 [00:00<00:10, 48.05it/s]

You are a clinical language model helping with abbreviation disambiguation in biomedical texts.
Text snippet (with acronym): velvet antlers vas are commonly used in traditional chinese medicine and invigorant and contain many PET components for health promotion the velvet antler peptide svap is one of active components in vas based on structural study the svap interacts with tgfÎ² receptors and disrupts the tgfÎ² pathway we hypothesized that svap prevents cardiac fibrosis from pressure overload by blocking tgfÎ² signaling SDRs underwent TAC tac or a sham operation T3 one month rats received either svap mgkgday or vehicle for an additional one month tac surgery induced significant cardiac dysfunction FB activation and fibrosis these effects were improved by treatment with svap in the heart tissue tac remarkably increased the expression of tgfÎ² and connective tissue growth factor ctgf ROS species C2 and the phosphorylation C2 of smad and ERK kinases erk svap inhibited the increases in r

Running Few-Shot Inference with BioGPT:   3%|▎         | 17/500 [00:00<00:09, 52.08it/s]

⚠️ Skipping index 10 due to input length (1289 tokens)
You are a clinical language model helping with abbreviation disambiguation in biomedical texts.
Text snippet (with acronym): velvet antlers vas are commonly used in traditional chinese medicine and invigorant and contain many PET components for health promotion the velvet antler peptide svap is one of active components in vas based on structural study the svap interacts with tgfÎ² receptors and disrupts the tgfÎ² pathway we hypothesized that svap prevents cardiac fibrosis from pressure overload by blocking tgfÎ² signaling SDRs underwent TAC tac or a sham operation T3 one month rats received either svap mgkgday or vehicle for an additional one month tac surgery induced significant cardiac dysfunction FB activation and fibrosis these effects were improved by treatment with svap in the heart tissue tac remarkably increased the expression of tgfÎ² and connective tissue growth factor ctgf ROS species C2 and the phosphorylation C2 of sma

Running Few-Shot Inference with BioGPT:   6%|▌         | 29/500 [00:00<00:09, 51.09it/s]

...

⚠️ Skipping index 287 due to input length (1348 tokens)
You are a clinical language model helping with abbreviation disambiguation in biomedical texts.
Text snippet (with acronym): velvet antlers vas are commonly used in traditional chinese medicine and invigorant and contain many PET components for health promotion the velvet antler peptide svap is one of active components in vas based on structural study the svap interacts with tgfÎ² receptors and disrupts the tgfÎ² pathway we hypothesized that svap prevents cardiac fibrosis from pressure overload by blocking tgfÎ² signaling SDRs underwent TAC tac or a sham operation T3 one month rats received either svap mgkgday or vehicle for an additional one month tac surgery induced significant cardiac dysfunction FB activation and fibrosis these effects were improved by treatment with svap in the heart tissue tac remarkably increased the expression of tgfÎ² and connective tissue growth factor ctgf ROS species C2 and the phosphorylation C2 of sm

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-20-fbc3d6e869c5>", line 113, in <cell line: 0>
    inputs = tokenizer(full_prompt, return_tensors="pt").to(device)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 2887, in __call__
    encodings = self._call_one(text=text, text_pair=text_pair, **all_kwargs)
                ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 2997, in _call_one
    return self.encode_plus(
           ^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 3073, in encode_plus
    return self._encode_plus(
           ^^^^^^^^^^^^^^

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-20-fbc3d6e869c5>", line 113, in <cell line: 0>
    inputs = tokenizer(full_prompt, return_tensors="pt").to(device)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 2887, in __call__
    encodings = self._call_one(text=text, text_pair=text_pair, **all_kwargs)
                ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 2997, in _call_one
    return self.encode_plus(
           ^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py", line 3073, in encode_plus
    return self._encode_plus(
           ^^^^^^^^^^^^^^

In [ ]:
pip install sacremoses

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 14.8 MB/s eta 0:00:00
